### Amazon Redshift ML integration with Amazon Bedrock

#### Pre-requisites

1. Please go through pre-requisites in the [blog](https://aws.amazon.com/blogs/big-data/integrate-amazon-bedrock-with-amazon-redshift-ml-for-generative-ai-applications/)
2. Enable LLM access.  Refer **Enable LLM model access** section in the [blog](https://aws.amazon.com/blogs/big-data/integrate-amazon-bedrock-with-amazon-redshift-ml-for-generative-ai-applications/)

Create patient information table

In [0]:
CREATE TABLE patientsinfo 
( pid integer ENCODE az64, 
pname varchar(100), 
condition character varying(100) ENCODE lzo, 
medication character varying(100) ENCODE lzo ) 
DISTSTYLE AUTO;

Load data into patient information table.

Download the [sample file](https://aws-blogs-artifacts-public.s3.amazonaws.com/artifacts/sample_patientsinfo.csv), upload into your S3 bucket and load data into patientsinfo table using the below COPY command

In [0]:
COPY patientsinfo
FROM 's3://sontitut/sample_patientsinfo.csv'
IAM_ROLE DEFAULT
csv
DELIMITER ','
IGNOREHEADER 1;

Prepare prompt

In [0]:
-- See sample data
select * from patientsinfo;

-- Aggregate the medication and conditions data
SELECT pname, 
listagg(distinct condition,',') within group (order by pid) over (partition by pid) as conditions,
listagg(distinct medication,',') within group (order by pid) over (partition by pid) as medications
FROM patientsinfo;

Build the prompt combining patient, conditions and medications data.

In [0]:
SELECT
pname || ' has ' || conditions || ' taking ' || medications as patient_prompt 
FROM (
    SELECT pname, 
    listagg(distinct condition,',') within group (order by pid) over (partition by pid) as conditions,
    listagg(distinct medication,',') within group (order by pid) over (partition by pid) as medications
    FROM patientsinfo) 
GROUP BY 1;

Create a materialized view with prompt.

Please note that you may see a message indicating that materialized views with column aliases will not be incrementally refreshed. You can safely ignore this message for the purpose of this illustration.

In [0]:
CREATE MATERIALIZED VIEW mv_prompts AUTO REFRESH YES 
AS 
(
    SELECT pid,
    pname || ' has ' || conditions || ' taking ' || medications as patient_prompt 
    FROM (
        SELECT pname, pid,
        listagg(distinct condition,',') within group (order by pid) over (partition by pid) as conditions,
        listagg(distinct medication,',') within group (order by pid) over (partition by pid) as medications
        FROM patientsinfo) 
    GROUP BY 1,2
)

Run query to view prompt from materialized view

In [0]:
SELECT * FROM mv_prompts;

Create External Model that leverages Bedrock Anthropic Claude

In [0]:
CREATE EXTERNAL MODEL patient_recommendations_h
FUNCTION patient_recommendations_func_h
IAM_ROLE 'arn:aws:iam::445818506882:role/brockiampolicy'
MODEL_TYPE BEDROCK
SETTINGS (
    MODEL_ID 'anthropic.claude-3-haiku-20240307-v1:0',
    PROMPT 'Generate personalized diet plan for following patient:');

Run predictions with the External Model created

In [0]:
SELECT patient_recommendations_func_h(patient_prompt) 
FROM mv_prompts 
where pid=101;

**Further options to customize**

Inference functions as leader-only functions

In [0]:
SELECT patient_recommendations_func_h('Generate diet plan for pre-diabetes');

Inference with UNIFIED request type models

In [0]:
--With temperature 0.2

SELECT patient_recommendations_func_h(patient_prompt,object('temperature', 0.2)) 
FROM mv_prompts
WHERE pid=101;

--with temperature 0.8

SELECT patient_recommendations_func_h(patient_prompt,object('temperature', 0.8)) 
FROM mv_prompts
WHERE pid=101;

Inference with RAW request type models

In [0]:
-- Create model with REQUEST_TYPE as RAW

CREATE EXTERNAL MODEL titan_raw
FUNCTION func_titan_raw
IAM_ROLE 'arn:aws:iam::445818506882:role/brockiampolicy'
MODEL_TYPE BEDROCK
SETTINGS (
    MODEL_ID 'amazon.titan-text-express-v1',
    REQUEST_TYPE RAW,
    RESPONSE_TYPE SUPER);
    
    
-- Need to construct the request during inference.
SELECT func_titan_raw(object('inputText', 'Generate personalized diet plan for following: ' || patient_prompt, 'textGenerationConfig', object('temperature', 0.5, 'maxTokenCount', 500)))
FROM mv_prompts limit 1;

Fetch run metrics withe RESPONSE_TYPE as SUPER

In [0]:
CREATE EXTERNAL MODEL patient_recommendations_v2
FUNCTION patient_recommendations_func_v2
IAM_ROLE 'arn:aws:iam::445818506882:role/brockiampolicy'
MODEL_TYPE BEDROCK
SETTINGS (
    MODEL_ID 'anthropic.claude-v2',
    PROMPT 'Generate personalized diet plan for following patient:',
    RESPONSE_TYPE SUPER);
    
-- Run the inference function   
SELECT patient_recommendations_func_v2(patient_prompt)
FROM mv_prompts limit 1;

Cleanup 

 To avoid incurring future charges, delete the Redshift Serverless instance or Redshift provisioned data warehouse created as part of the pre-requisite steps.